<a href="https://colab.research.google.com/github/tsimut/Final-Project/blob/master/topic_modelling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
pip install spacy

In [2]:
pip install pyLDAvis

     |████████████████████████████████| 1.6MB 5.0MB/s 
  Stored in directory: /root/.cache/pip/wheels/98/71/24/513a99e58bb6b8465bae4d2d5e9dba8f0bef8179e3051ac414
Successfully built pyLDAvis


In [0]:
import nltk
from nltk import FreqDist
import pandas as pd
pd.set_option("display.max_colwidth", 200)
import numpy as np
import re
import spacy
import gensim
from gensim import corpora
import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
from bs4 import BeautifulSoup
import requests
import time
import nltk
from nltk.corpus import stopwords

In [0]:
review=[]
rating=[]

In [5]:
#USE BEAUTIFUL SOUP TO SCRAPE REVIEWS FROM WEBSITE AND APPEND THE DATA TO LISTS
page_count = 0
while page_count <10:
    
    url = "https://www.consumeraffairs.com/finance/royal_bank.html?page=%s" %(page_count)
    page = requests.get(url)
    soup = BeautifulSoup(page.content, 'html.parser')
    reviews=soup.find(id="reviews-container")
    
    comments=soup.find_all("div", class_="rvw-bd ca-txt-bd-2")
    for ct in comments:
        review.append(ct.find("p").get_text())
    
    star=reviews.find_all("div",class_="rvw__hdr-stat") 
    for st in star:
        try:
            rating.append(st.find("img")["data-rating"])
        except:
            rating.append(print("none"))
       
    page_count += 1

none
none


In [6]:
len(rating)

300

In [7]:
Reviews = pd.DataFrame({
"Review":review,    
"Rating":rating
})


Reviews.head(20)

Review Rating
0   We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...    5.0
1   I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...    4.0
2   We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...    4.0
3   I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...    1.0
4   What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...    1.0
5   Today I heard from the Manager.  He was exceptionally good and dealt with all my concerns.  He explained some of the reasons for the mishaps and how they will be rectified.  I feel very good about...   None
6   Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...    1.0
7   Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...    1.0
8   I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...    2.0
9   Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...    1.0
10  Business owners stay away from this place. An hour long interview for a $5000 credit card and then tons of signatures. After 2 weeks I was again called back to bank to sign some more stupid papers...    1.0
11  The bank put a deposit only message on my account, I went into the branch on Monday to have it removed. I was told the manager would review my account the next morning and contact me by the end of...    1.0
12  I have a business account with RBC. I called them to request a line of credit. After wasting about an hour on the phone, the person I was talking to (he said his name is Jay) asked me to be on hol...    1.0
13  The franchising come with everything in a neat package. Then little by little they start revoke credit cards and lines of credit. When that doesn’t make you quite they close bank account send lett...    1.0
14  If RBC read any of these reviews they would have a better understanding that their customers DO NOT want virtual freaking customer service and wish to speak to a live person. Hire more people to d...    1.0
15  I have business account with RBC. Where I deposit cheques every month and all the cheques are from same one client! They been putting it on hold for 24 hours! Which was ok and now they started hol...    1.0
16  I applied for a mortgage at RBC. They advertise that their mortgage approval takes from 60 seconds to 3 hours. More than 2 weeks passed and they even didn't notify me that it was denied. So I've l...    1.0
17  I have been RBC client for over 12 years, with the good background history with good income. I tried to apply for any service such as personal loan and line of credit but I was denied. It is a sha...    1.0
18  I opened my account just recently at a branch in Dundas and Spadina last month. I plan to use it after a month, once I joined my next job at a new company. The advisor gave me a void c

In [0]:
# remove unwanted characters, numbers and symbols
Reviews['Clean Reviews'] = Reviews['Review'].str.replace("[^a-zA-Z#]", " ")

In [0]:
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x.lower() for x in x.split()))

In [10]:
# remove short words (length < 3)
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: ' '.join([w for w in x.split() if len(w)>2]))

Reviews['Clean Reviews'].head()

0    met ratna june move calgary that time both just got our jobs somehow had dream buy our own house calgary were new this town and looking for someone help buying house already had account rbc just g...
1    have found their staff extremely helpful having worked many financial institutions can honestly agree that customers are more likely provide bad review than take the time write good review when wa...
2    opened two accounts with rbc jamie the salmon arm branch spent hrs with first opening savings account and then high interest account she was very patient and walked through online banking explaini...
3    have banked with rbc for years and was looking consolidate debt they told that probably wouldn able get home equity loan despite having least equity and that consolidation loan would not save much...
4    what pos these pvqa are this idiotic piece software has decided its tiny brain that computer longer recognised secure and keeps bombarding with these questions whenever try si

In [11]:
import nltk
nltk.download('stopwords')
stop = stopwords.words('english')
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x for x in x.split() if x not in stop))
Reviews['Clean Reviews']

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


0      met ratna june move calgary time got jobs somehow dream buy house calgary new town looking someone help buying house already account rbc gave call customer service referred ratna name met person e...
1      found staff extremely helpful worked many financial institutions honestly agree customers likely provide bad review take time write good review warranted dealt royal bank past found staff offered ...
2      opened two accounts rbc jamie salmon arm branch spent hrs first opening savings account high interest account patient walked online banking explaining every step detailed user friendly manner expl...
3      banked rbc years looking consolidate debt told probably able get home equity loan despite least equity consolidation loan would save much money suggested apply visa balance transfer months may get...
4      pos pvqa idiotic piece software decided tiny brain computer longer recognised secure keeps bombarding questions whenever try sign truly disgusting worst security sof

In [12]:
#IDENTIFY TOP 10 OCCURING WORDS
freq = pd.Series(' '.join(Reviews['Clean Reviews']).split()).value_counts()[:10]
freq

rbc        402
bank       368
account    295
credit     179
money      135
years      127
told       123
get        117
branch     116
card       113
dtype: int64

In [0]:
common_word=("rbc","told","get","bank","banking","royal")

def remove_commonwords(rev):
    rev_new = " ".join([i for i in rev if i not in common_word])
    return rev_new


In [0]:
reviews = [remove_commonwords(r.split()) for r in Reviews['Clean Reviews']]

In [15]:
reviews

['met ratna june move calgary time got jobs somehow dream buy house calgary new town looking someone help buying house already account gave call customer service referred ratna name met person expressed desire buy new house nice asked four pay stubs processed mortgage pre approval says wait another three months become permanent status employment',
 'found staff extremely helpful worked many financial institutions honestly agree customers likely provide bad review take time write good review warranted dealt royal past found staff offered products suited needs made suggestions even ask wealthy perfect credit',
 'opened two accounts jamie salmon arm branch spent hrs first opening savings account high interest account patient walked online banking explaining every step detailed user friendly manner explained various services costs disadvantages advantages friendly professional manner departed client cards canadian mastercard high interest savings account visa card applications deposited mo

In [0]:
nlp = spacy.load('en', disable=['parser', 'ner'])

def lemmatization(texts, tags=['NOUN', 'ADJ']):
  output = []
  for sent in texts:
    doc = nlp(" ".join(sent)) 
    output.append([token.lemma_ for token in doc if token.pos_ in tags])
  return output


In [0]:
tokenized_reviews = pd.Series(reviews).apply(lambda x: x.split())

In [0]:
lemma_reviews= lemmatization(tokenized_reviews)

In [19]:
lemma_reviews

[['ratna',
  'june',
  'calgary',
  'time',
  'job',
  'house',
  'calgary',
  'new',
  'town',
  'someone',
  'help',
  'house',
  'account',
  'call',
  'customer',
  'service',
  'ratna',
  'name',
  'person',
  'desire',
  'new',
  'house',
  'nice',
  'pay',
  'stub',
  'mortgage',
  'pre',
  'approval',
  'month',
  'permanent',
  'status',
  'employment'],
 ['staff',
  'helpful',
  'many',
  'financial',
  'institution',
  'customer',
  'bad',
  'review',
  'time',
  'good',
  'review',
  'royal',
  'past',
  'staff',
  'product',
  'need',
  'suggestion',
  'wealthy',
  'perfect',
  'credit'],
 ['account',
  'jamie',
  'salmon',
  'arm',
  'branch',
  'hrs',
  'first',
  'opening',
  'saving',
  'high',
  'interest',
  'account',
  'patient',
  'online',
  'banking',
  'step',
  'user',
  'friendly',
  'manner',
  'various',
  'service',
  'cost',
  'advantage',
  'friendly',
  'professional',
  'manner',
  'client',
  'card',
  'canadian',
  'mastercard',
  'high',
  'interest

In [44]:
from gensim.models import Phrases
bigram = Phrases(lemma_reviews, min_count=3)
for idx in range(len(lemma_reviews)):
    for token in bigram[lemma_reviews[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            lemma_reviews[idx].append(token)

/usr/local/lib/python3.6/dist-packages/gensim/models/phrases.py:598: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


In [0]:
#Remove rare and common tokens.

from gensim.corpora import Dictionary

# Create a dictionary representation of the documents.
dictionary = Dictionary(lemma_reviews)

# Filter out words that occur less than 20 documents, or more than 50% of the documents.
dictionary.filter_extremes(no_below=20, no_above=0.5)

In [0]:
# Vectorize data.

# Bag-of-words representation of the documents.
corpus = [dictionary.doc2bow(doc) for doc in lemma_reviews]


In [0]:
def tuple_ith_element(lst, element=1):
    return [x[element] for x in lst]


def split_test_train(crps, test_prop=0.7):
    in_train = numpy.random.choice(len(crps), size=int(len(crps)*test_prop), replace=False)
    tr = [crps[i] for i in  in_train]
    ix = range(len(crps))
    s = set(in_train)
    in_test = [i for i in ix if i not in s]
    ts = [crps[i] for i in in_test]

    return tr, ts


def search_param_space(corpus_iter, dict_iter, parallel=False,
                       metric = 'coherence', ntopics=[5], num_passes=1):
    ''' fit LDA model, with faster option using multicore implementation
        and calculate topic coherence for each K
    '''
    result = dict()

    if metric not in ['coherence', 'log_perplexity']:
        raise ValueError("Metric can only be 'coherence' or 'log_perplexity'")

    # split into training and testing sets
    train_corpus, test_corpus = split_test_train(corpus_iter)

    # iterate through topic list and fit a model for each
    for t in ntopics:
      if parallel:
        lda_mod = LdaMulticore(train_corpus, id2word=dict_iter, num_topics=t, passes=num_passes)
      else:
        lda_mod = LdaModel(train_corpus, id2word=dict_iter, num_topics=t, alpha='auto', passes=num_passes)

      if metric=='coherence':
        topic_coh = tuple_ith_element(lda_mod.top_topics(test_corpus, num_words=20))
        result[str(t)] = numpy.mean(topic_coh)

      elif metric=='log_perplexity':
          result[str(t)] = lda_mod.log_perplexity(test_corpus)

    return result

In [35]:
import numpy 
topic_search =numpy.arange(2, 20)
print (topic_search)

topic_coherence = search_param_space(corpus_iter=corpus, dict_iter=dictionary, parallel=True,
                                     metric='coherence', ntopics=topic_search, num_passes=10)

[ 2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]


NameError: ignored

In [34]:
plt.rcParams['figure.figsize'] = (10,5)
x = tuple_ith_element(sorted(topic_coherence.items(), key=lambda x: x[1]))
labels = tuple_ith_element(sorted(topic_coherence.items(), key=lambda x: x[1]),0)
xticklabels = ['K='+t.replace('_auto','') for t in labels ]
plt.plot(range(len(x)), x)
plt.xticks(range(len(x)), xticklabels, rotation=70)
plt.ylabel('Topic Coherence')
plt.show()

NameError: ignored

In [47]:
# Creating the object for LDA model using gensim library
LDA = gensim.models.ldamodel.LdaModel
# Build LDA model
lda_model = LDA(corpus=corpus, id2word=dictionary, num_topics=5, random_state=100,
                chunksize=1000, passes=50)

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for

In [50]:
lda_model.print_topics()

[(0,
  '0.124*"customer" + 0.100*"service" + 0.065*"call" + 0.053*"time" + 0.048*"customer_service" + 0.045*"phone" + 0.039*"hour" + 0.032*"people" + 0.031*"business" + 0.029*"mortgage"'),
 (1,
  '0.140*"card" + 0.117*"credit" + 0.075*"account" + 0.070*"credit_card" + 0.050*"fee" + 0.048*"payment" + 0.048*"year" + 0.042*"charge" + 0.035*"visa" + 0.032*"month"'),
 (2,
  '0.203*"account" + 0.059*"year" + 0.044*"month" + 0.044*"new" + 0.042*"mortgage" + 0.042*"fund" + 0.041*"branch" + 0.035*"client" + 0.030*"time" + 0.030*"letter"'),
 (3,
  '0.104*"loan" + 0.097*"credit" + 0.094*"line" + 0.063*"interest" + 0.056*"money" + 0.055*"mortgage" + 0.051*"year" + 0.050*"line_credit" + 0.043*"business" + 0.035*"pay"'),
 (4,
  '0.097*"branch" + 0.081*"check" + 0.081*"day" + 0.072*"manager" + 0.068*"money" + 0.065*"account" + 0.058*"cheque" + 0.052*"teller" + 0.051*"deposit" + 0.040*"time"')]

In [51]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
vis

/usr/local/lib/python3.6/dist-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2      0.032817  0.036026       1        1  24.410694
1     -0.087311  0.132747       2        1  23.903502
0      0.087051 -0.256666       3        1  19.284842
4      0.211835  0.118869       4        1  16.252861
3     -0.244392 -0.030976       5        1  16.148096, topic_info=   Category        Freq              Term       Total  loglift  logprob
17  Default  134.000000              card  134.000000  30.0000  30.0000
0   Default  314.000000           account  314.000000  29.0000  29.0000
12  Default  177.000000            credit  177.000000  28.0000  28.0000
2   Default  104.000000          customer  104.000000  27.0000  27.0000
9   Default   82.000000           service   82.000000  26.0000  26.0000
25  Default   72.000000              loan   72.000000  25.0000  25.0000
38  Default   64.000000              line   64.000000  24.0000  24.0000
70  Default   53.000000             check   53.000000  23.0000  23.0000
54  Default   67.000000       credit_card   67.000000  22.0000  22.0000
16  Default  118.000000            branch  118.000000  21.0000  21.0000
29  Default   57.000000           manager   57.000000  20.0000  20.0000
61  Default   38.000000            cheque   38.000000  19.0000  19.0000
21  Default   48.000000          interest   48.000000  18.0000  18.0000
50  Default   93.000000               day   93.000000  17.0000  17.0000
1   Default   59.000000              call   59.000000  16.0000  16.0000
71  Default   34.000000            teller   34.000000  15.0000  15.0000
3   Default   38.000000  customer_service   38.000000  14.0000  14.0000
44  Default   51.000000               fee   51.000000  13.0000  13.0000
39  Default   33.000000       line_credit   33.000000  12.0000  12.0000
5   Default   99.000000          mortgage   99.000000  11.0000  11.0000
55  Default   38.000000           deposit   38.000000  10.0000  10.0000
34  Default   47.000000              fund   47.000000   9.0000   9.0000
6   Default   52.000000               new   52.000000   8.0000   8.0000
46  Default   42.000000             phone   42.000000   7.0000   7.0000
42  Default   46.000000            charge   46.000000   6.0000   6.0000
66  Default   84.000000           payment   84.000000   5.0000   5.0000
56  Default   28.000000              next   28.000000   4.0000   4.0000
26  Default  134.000000             money  134.000000   3.0000   3.0000
23  Default   32.000000              debt   32.000000   2.0000   2.0000
52  Default   41.000000              hour   41.000000   1.0000   1.0000
..      ...         ...               ...         ...      ...      ...
38   Topic5   60.720642              line   64.973091   1.7557  -2.3621
25   Topic5   66.718857              loan   72.926483   1.7344  -2.2679
21   Topic5   40.375034          interest   48.883724   1.6321  -2.7702
23   Topic5   22.284395              debt   32.817047   1.4363  -3.3645
20   Topic5   16.544207              high   25.818277   1.3783  -3.6624
69   Topic5   21.874407         insurance   35.716557   1.3331  -3.3831
63   Topic5   13.319495            amount   32.798061   0.9222  -3.8792
64   Topic5   10.688426            canada   27.565029   0.8760  -4.0993
14   Topic5   19.456148              good   52.217270   0.8361  -3.5003
5    Topic5   35.494015          mortgage   99.335037   0.7942  -2.8991
12   Topic5   62.613998            credit  177.731873   0.7801  -2.3314
49   Topic5   13.804357          personal   39.306641   0.7770  -3.8434
13   Topic5   10.010944         financial   28.552399   0.7753  -4.1648
7    Topic5   22.621477               pay   66.150665   0.7503  -3.3495
41   Topic5   27.907448          business   85.652657   0.7020  -3.1395
43   Topic5   14.946520           company   49.304726   0.6298  -3.7640
68   Topic5    6.631724            dollar   23.682064   0.5505  -4.5766
26   Topic5   36.224342             money  134.2527

In [0]:
import pickle

In [0]:
filename = 'finalized_model.sav'
pickle.dump(lda_model, open(filename, 'wb'))

In [0]:
from google.colab import drive
drive.mount('/content/drive')

In [0]:
!ls /content/gdrive/My Drive

ls: cannot access '/content/gdrive/My': No such file or directory
ls: cannot access 'Drive': No such file or directory


In [0]:
model_save_name = lda_model

In [0]:
!pip install -q torch==1.1.0 torchvision

In [0]:
import torch

In [0]:
path = F"/content/gdrive/My Drive/{model_save_name}" 
torch.save(lda_model, path)

In [0]:
model


In [0]:
name_dict = {   0: "Issues with Route", # 1 on the chart
                1: "Issues with payment/refund",    # 2 on the chart
                2: "Issues with time",  # 3 on the chart
            }

In [0]:
scored = model[doc_term_matrix]


In [0]:
topic_prob = map(lambda x: max(x, key=lambda item: item[1]), scored)
scored_reviews = pd.DataFrame(zip(reviews, topic_prob), columns=['Review', 'Main_Topic'])
scored_reviews[['Topic', 'Prob']] = scored_reviews['Main_Topic'].apply(pd.Series)
scored_reviews['Topic Name'] = scored_reviews['Topic'].map(name_dict)

In [0]:
scored_reviews

Review  ...                  Topic Name
0    great experiences couple bad experiences worst experience picked emergency situation needed hospital visit someone hurry already highway realized reeked alcohol completely intoxicated weaving lane...  ...  Issues with payment/refund
1    never lyft cab company highly ineffective oddly enough attracted highly qualified polite earn extra money enjoy scheduling simple smartphone application detects local via gps directs closest avail...  ...            Issues with time
2    never negative experience one downloaded first college one continue past years experiences better others opinion probably worse experience rides enjoyed ones respected privacy acted courteously pr...  ...  Issues with payment/refund
3    always skeptical rideshare services news reports assaults robberies company first time earlier year trip conference las vegas first excellent completed without problem second little scary requeste...  ...            Issues with time
4    several times far happy company easy set account love constantly upgrading features company making customer feel safe taking arrive timely manner professional love add feature signals letting know...  ...  Issues with payment/refund
5    trip last years overall rating excellent riders reviews account time call customer support team problems expect ever listen last week rider vomited peed inside vehicle refused send cleaning fee ta...  ...            Issues with time
6                           first time called says make cancel wont charged cancelled charged horse richland miss jackson miss area told cancel like take job could make dollars nothing piece nissan altima  ...            Issues with time
7                           lip service term quality india large number cars dirty acs hardly fictional trying defraud overcharge customer support india dismal overcharge rupees offered refund rupees joke  ...           Issues with Route
8    requested fort worth south henderson street irving texas upfront fare showed economy said offer max per discount aashish toyota corolla came literally said going home got exactly close home conven...  ...           Issues with Route
9                         earlier great provide prompt customer service quick redressal issues person speak acknowledgement even complain random multiple charges deducted trip thank god ola otherwise scam  ...  Issues with payment/refund
10   rider good passenger rating never issues experience general good month ago disabled account reached customer support email exchanges customer support sent rude offensive email violated terms condi...  ...  Issues with payment/refund
11                                             eats cancel order without refund ubereats friends order food eats money deliver food experience story customer support resolve problem delivery boy come home  ...            Issues with time
12   took igt sector noida shows rent approx premier looks good reached location without stoppage asked pay rupees totally disappointing prepaid taxi outside airport even charging rupees cross checked ...  ...            Issues with time
13   husband thought let everybody know experience new orleans never take went vacation new orleans take cruise arrived day suggestion travel agent make sure nothing went wrong new comfort inn suites n...  ...  Issues with payment/refund
14   montreal last week raining wanted quick destination booked amount displayed included surge mind running late wanted destination time unfortunately event taking place location cops blocked roads du...  ...           Issues with Route
15        launched app quoted mile home expected paid generally dozens times got picked later billed triple quote says confirmed change would ever could taken limo less dispute denied shut pay fired never  ...           Issues with Route
16   placed order eats food never showed charged anyways called tell customer service reps ignored food never showed eat lunch gave last money eat today